In [129]:
import sys
import requests
import json
import pandas as pd
import numpy as np
from tqdm import tqdm
import time
from flatten_json import flatten

In [9]:
API_KEY = 'v2wsp3yB5OWqhGf99uzEpFaGwddFnyCh'

In [10]:
import sys
import json
import requests

API_SIGNUP_URL = 'https://developer.nytimes.com/get-started'

class ArchiveAPI():
    def __init__(self, key):
        if key is None:
            raise Exception('Must provide an API key. If you don\'t have one, go to \\
            {} to sign up for one'.format(API_SIGNUP_URL))
        else:
            self.key = key
            
    def fetch_articles(self, month, year):
        """
        month: integer 1-12
        year : integer 1851-2019
        
        returns a request object
        """
        #Make sure inputs are good
        if not isinstance(month,int):
            raise ValueError('Month needs to be an integer')
        if not isinstance(year, int):
            raise ValueError('Year needs to be an integer')
        if month < 1 or month > 12:
            raise ValueError('Month needs to be 1-12')
        if year < 1851 or year > 2019:
            raise ValueError('Year needs to be 1851 - 2019')
        
        #Make call to API and get a response
        resp = requests.get('https://api.nytimes.com/svc/archive/v1/{}/{}.json?api-key={}'.format(year,month,self.key))
        try:
            if resp.status_code != 200:
                print("Error:")
                if resp.status_code == 401:
                    raise Exception('Unauthorized request, check api-key is set.')
                if resp.status_code == 429:
                    raise Exception('Too many requests. You reached your per minute or per day rate limit.')
            else:
                print("Response for {}/{}".format(month, year))
                return resp
        except Exception as exc:
            print('{} for {}/{}'.format(exc, month, year))
            
    def fetch_all_articles(self):
        """
        Returns all articles since 1851
        """
        responses = []
        print('Got responses for:\n')
        for month in np.arange(1,13):
            for year in np.arange(1851,2020):
                time.sleep(6)
                try:
                    responses = self.fetch_articles()
                    print('\t{}/{}'.format(month,year))
                except Exception as exc:    
                    print('Exception raised for {}/{}:\n{}'.format(month,year,exc))
                

                responses.append(resp)
                
    def resp_to_df(self, resp):
        article_metadata_array = resp.json()['response']['docs']
        
                

    def json_to_dataframe(self, json_file):
        """
        json_file:  a .json file which has been pulled from the Archive API and serialized in JSON format.
        """
        with open(json_file) as json_file:  
            data = json.load(json_file)
        return pd.DataFrame.from_dict(data['docs'])

    

# if __name__ == '__main__':
#     print(sys.argv)
#     if len(sys.argv) != 4:
#         raise IOError('User must specify API key, month, and year')
#     API_KEY,MONTH,YEAR = sys.argv[1:]
#     #TODO check that inputs are valid.
#     archiveAPI = ArchiveAPI(API_KEY)
#     articles = archiveAPI.fetch_articles(MONTH, YEAR)

#     #TODO allow user to specify output dir
#     with open('response.json', 'w') as outfile:
#         json.dump(articles.json()['response'], outfile)


### TODO Write TEST

In [16]:
MONTH, YEAR = 11,1852
archiveAPI = ArchiveAPI(API_KEY)
articles = archiveAPI.fetch_articles(MONTH, YEAR)

Response for 11/1852


In [32]:
n_articles = articles.json()['response']['meta']['hits']
n_articles

2063

In [37]:
article_metadata_array = articles.json()['response']['docs']

In [42]:
columns = list(article_metadata_array[-1].keys())
columns

['web_url',
 'snippet',
 'lead_paragraph',
 'abstract',
 'print_page',
 'blog',
 'source',
 'multimedia',
 'headline',
 'keywords',
 'pub_date',
 'document_type',
 'news_desk',
 'section_name',
 'subsection_name',
 'byline',
 'type_of_material',
 '_id',
 'word_count',
 'slideshow_credits']

In [73]:
df = pd.DataFrame(columns = columns)
start= time.time()
for article_metadata in article_metadata_array:
    df = df.append(article_metadata, ignore_index=True)
print('Took {} seconds'.format(time.time() - start))
df.iloc[0]

Took 11.61848497390747 seconds


web_url              https://query.nytimes.com/gst/abstract.html?re...
snippet              MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN...
lead_paragraph       MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN...
abstract                                                          None
print_page                                                           1
blog                                                                []
source                                              The New York Times
multimedia                                                          []
headline             {'main': 'Front Page 2 -- No Title', 'kicker':...
keywords                                                            []
pub_date                                          1852-11-01T00:03:58Z
document_type                                                  article
news_desk                                                         None
section_name                                                      None
subsec

In [139]:
start = time.time()
article_meta_data_array_flattened = (flatten(d) for d in article_metadata_array)
print('Took {} seconds'.format(time.time() - start))

Took 7.724761962890625e-05 seconds


In [140]:
df_flat = pd.DataFrame(article_meta_data_array_flattened)

In [142]:
df_flat.iloc[0]

_id                                                      4fbfd31345c1498b0d009319
abstract                                                                     None
blog                                                                           []
byline                                                                        NaN
byline_organization                                                           NaN
byline_original                                                               NaN
byline_person                                                                 NaN
byline_person_0_firstname                                                     NaN
byline_person_0_lastname                                                      NaN
byline_person_0_middlename                                                    NaN
byline_person_0_organization                                                  NaN
byline_person_0_rank                                                          NaN
byline_person_0_

In [85]:
for key in df.columns:
    print(key, df.iloc[0][key], '\n')

web_url https://query.nytimes.com/gst/abstract.html?res=9D0CEEDF1438E334BC4953DFB7678389649FDE 

snippet MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN has gone to Ohio, it is said by a correspondent of the Baltimore Sun. to east his vote for the Whig 'candidate for the Presidency. It is Mr. C.'s purpose, if a suitable opportunity presents itself, to... 

lead_paragraph MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN has gone to Ohio, it is said by a correspondent of the Baltimore Sun. to east his vote for the Whig 'candidate for the Presidency. It is Mr. C.'s purpose, if a suitable opportunity presents itself, to vindicate him self before his former constituents from the charges of Dr. OLDs as to the GARDINER claim. 

abstract None 

print_page 1 

blog [] 

source The New York Times 

multimedia [] 

headline {'main': 'Front Page 2 -- No Title', 'kicker': '1'} 

keywords [] 

pub_date 1852-11-01T00:03:58Z 

document_type article 

news_desk None 

section_name None 

subsection_name N

In [108]:
flat = flatten

In [114]:
df_2.columns

Index(['_id', 'abstract', 'blog', 'byline', 'byline.organization',
       'byline.original', 'byline.person', 'document_type', 'headline.kicker',
       'headline.main', 'keywords', 'lead_paragraph', 'multimedia',
       'news_desk', 'print_page', 'pub_date', 'section_name',
       'slideshow_credits', 'snippet', 'source', 'subsection_name',
       'type_of_material', 'web_url', 'word_count'],
      dtype='object')

In [112]:
df_3.head()

_id abstract blog  \
0  4fbfd31345c1498b0d009319     None   []   
1  4fbfd31b45c1498b0d009617     None   []   
2  4fbfd33345c1498b0d009ca7     None   []   
3  4fbfd34f45c1498b0d00a456     None   []   
4  4fbfd34f45c1498b0d00a45f     None   []   

                                              byline document_type  \
0                                               None       article   
1  {'person': [{'organization': '', 'role': 'repo...       article   
2                                               None       article   
3                                               None       article   
4                                               None       article   

                                            headline keywords  \
0  {'main': 'Front Page 2 -- No Title', 'kicker':...       []   
1  {'main': 'SOUTH AMERICA.; Affairs at Rio Janei...       []   
2  {'main': 'Hon. Rufus Cheate for Scott and Grah...       []   
3        {'main': 'SPECIAL NOTICES.', 'kicker': '1'}       []   
4   {'main': 'Article 7 -- No Title', 'kicker': '1'}       []   

                                      lead_paragraph multimedia news_desk  \
0  MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN...         []      None   
1  On the 17th of August, His Imperial Majesty, D...         []      None   
2                                               None         []      None   
3                                               None         []      None   
4                                               None         []      None   

  print_page              pub_date section_name slideshow_credits  \
0          1  1852-11-01T00:03:58Z         None              None   
1          2  1852-11-01T00:03:58Z         None              None   
2          1  1852-11-01T00:03:58Z         None              None   
3          1  1852-11-01T00:03:58Z         None              None   
4          4  1852-11-01T00:03:58Z         None              None   

                                             snippet              source  \
0  MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN...  The New York Times   
1  On the 17th of August, His Imperial Majesty, D...  The New York Times   
2                                               None  The New York Times   
3                                               None  The New York Times   
4                                               None  The New York Times   

  subsection_name type_of_material  \
0            None       Front Page   
1            None          Article   
2            None       Front Page   
3            None       Front Page   
4            None          Article   

                                             web_url  word_count  
0  https://query.nytimes.com/gst/abstract.html?re...         256  
1  https://query.nytimes.com/gst/abstract.html?re...         528  
2  https://query.nytimes.com/gst/abstract.html?re...          55  
3  https://query.nytimes.com/gst/abstract.html?re...         293  
4  https://query.nytimes.com/gst/abstract.html?re...          22

In [98]:
article_metadata_array[:5]

[{'web_url': 'https://query.nytimes.com/gst/abstract.html?res=9D0CEEDF1438E334BC4953DFB7678389649FDE',
  'snippet': "MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN has gone to Ohio, it is said by a correspondent of the Baltimore Sun. to east his vote for the Whig 'candidate for the Presidency. It is Mr. C.'s purpose, if a suitable opportunity presents itself, to...",
  'lead_paragraph': "MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN has gone to Ohio, it is said by a correspondent of the Baltimore Sun. to east his vote for the Whig 'candidate for the Presidency. It is Mr. C.'s purpose, if a suitable opportunity presents itself, to vindicate him self before his former constituents from the charges of Dr. OLDs as to the GARDINER claim.",
  'abstract': None,
  'print_page': '1',
  'blog': [],
  'source': 'The New York Times',
  'multimedia': [],
  'headline': {'main': 'Front Page 2 -- No Title', 'kicker': '1'},
  'keywords': [],
  'pub_date': '1852-11-01T00:03:58Z',
  'document_type': 'ar

In [96]:
df_2.iloc[1]['byline.person']

[{'organization': '', 'role': 'reported', 'rank': 1}]

In [107]:
df_2['byline.person'].astype(str).unique()

array(['nan', "[{'organization': '', 'role': 'reported', 'rank': 1}]",
       "[{'organization': '', 'role': 'reported', 'rank': 1}, {'organization': '', 'role': 'reported', 'rank': 2}]",
       '[]',
       "[{'firstname': 'R.', 'middlename': 'N.', 'lastname': 'H', 'rank': 1, 'role': 'reported', 'organization': ''}]",
       "[{'firstname': 'J.', 'middlename': 'S.', 'lastname': 'SCOFIELD', 'rank': 1, 'role': 'reported', 'organization': ''}, {'organization': '', 'role': 'reported', 'rank': 2}]",
       '[{\'organization\': \'\', \'role\': \'reported\', \'rank\': 1, \'firstname\': "Dan\'l", \'lastname\': \'WEBSTER\'}]',
       "[{'organization': '', 'role': 'reported', 'rank': 1, 'firstname': 'L.', 'lastname': 'STEVENS'}]",
       "[{'organization': '', 'role': 'reported', 'rank': 1, 'firstname': 'Oration', 'lastname': 'REV'}]",
       "[{'firstname': 'Albert', 'middlename': 'H.', 'lastname': 'Nicolay', 'rank': 1, 'role': 'reported', 'organization': ''}]",
       "[{'firstname': 'X.', '

In [99]:
article_metadata_array_copy = np.copy(article_metadata_array)

In [104]:
orig_person_dic = article_metadata_array_copy[1]['byline']['person']
extra_dic_copy = extra_dic

[{'organization': '', 'role': 'reported', 'rank': 1}]

In [26]:
MONTH, YEAR = 9,2001
archiveAPI = ArchiveAPI(API_KEY)
responses = []
for i in np.arange(1,3):
    responses.append(archiveAPI.fetch_articles(i, YEAR))

Response for 1/2001
Response for 2/2001


In [47]:
responses[0].json() == data[0]

True

In [40]:
responses_json_strings = [response.json() for response in responses]

In [42]:
#TODO allow user to specify output dir
with open('responses.json', 'w') as outfile:
    json.dump(responses_json_strings, outfile)


In [43]:
with open('responses.json') as json_file:

    data = json.load(json_file)


In [44]:
data

[{'copyright': 'Copyright (c) 2013 The New York Times Company.  All Rights Reserved.',
  'response': {'meta': {'hits': 7736},
   'docs': [{'web_url': 'https://www.nytimes.com/2001/01/01/sports/sports-of-the-times-count-one-more-vote-for-the-ravens-defense.html',
     'snippet': "IN his moment of triumph yesterday, Brian Billick used the postgame podium to toss one final shot at Al Groh, the departed Jets head coach. Before the Jets' game against Baltimore a week earlier, Groh had been sarcastic in praising the Ravens' def...",
     'lead_paragraph': "IN his moment of triumph yesterday, Brian Billick used the postgame podium to toss one final shot at Al Groh, the departed Jets head coach. Before the Jets' game against Baltimore a week earlier, Groh had been sarcastic in praising the Ravens' defense, telling members of the news media how the Jets didn't have a chance. Yesterday, in the wake of the Ravens' 21-3 victory over Denver, Billick was asked how the Ravens' offense would attack th

In [12]:
API_KEY = 'v2wsp3yB5OWqhGf99uzEpFaGwddFnyCh'
API_SIGNUP_URL = 'https://developer.nytimes.com/get-started'

class ArchiveAPI():
    def __init__(self, key):
        if key is None:
            raise Exception('Must provide an API key. \
            If you don\'t have one, go to {} to sign up for one'\
                            .format(API_SIGNUP_URL))
        else:
            self.key = key
            
    def fetch_articles(self, month, year):
        """
        month: integer 1-12
        year : integer 1851-2019
        
        returns a request object
        """
        
        resp = requests.get('https://api.nytimes.com/svc/archive/v1/{}/{}.json?api-key={}'.format(year,month,self.key))
        print('inside fetch_articles')
        return resp
        try:
            if resp.status_code != 200:
                print("Error: resp.status_code = {}".format(resp.status_code))
                if resp.status_code == 401:
                    raise Exception('Unauthorized request, check\
                    api-key is set.')
                if resp.status_code == 429:
                    raise Exception('Too many requests. You reached \
                    your per minute or per day rate limit.')
            else: 
                return resp
        except:
            print('No Resp')
        
                            
        
        



In [20]:
if __name__ == '__main__':
    archiveAPI = ArchiveAPI(API_KEY)
    articles = archiveAPI.fetch_articles(9, 2001)
    
    

    
#     sys.argv.append('hello')
#     print(sys.argv)
#     api = ArchiveAPI('key')
#     api.fetch_articles('asdf','asdf')

inside fetch_articles


In [34]:
articles.json().keys()

dict_keys(['copyright', 'response'])

In [36]:
articles.json()['response']

{'meta': {'hits': 8297},
 'docs': [{'web_url': 'https://www.nytimes.com/2001/09/01/arts/edward-rivera-62-writer-and-teacher.html',
   'snippet': "Edward Rivera, the author of the autobiographical novel ''Family Installments: Memoirs of Growing Up Hispanic'' and an assistant professor at City College of New York, died on Aug. 25 in Manhattan, where he lived. He was 62.    The cause was a hea...",
   'lead_paragraph': "Edward Rivera, the author of the autobiographical novel ''Family Installments: Memoirs of Growing Up Hispanic'' and an assistant professor at City College of New York, died on Aug. 25 in Manhattan, where he lived. He was 62. The cause was a heart attack, said his brother Richard.",
   'abstract': 'Edward Rivera, author of autobiographical novel Family Installments: Memoirs of Growing Up Hispanic, and assistant professor at City College of New York, dies at age 62; photo (S)',
   'print_page': '15',
   'blog': [],
   'source': 'The New York Times',
   'multimedia': [],
   '

In [33]:
with open('response.json', 'w') as outfile:
    json.dump(articles.json()['response'], outfile)
# articles.json()['response']

In [22]:
for key, value in articles.headers.items():
    print ('Key: {} \t Value: {}'.format(key, value))

# type(resp.json())

# resp.json()['response'].keys()

# len(resp.json()['response']['docs'])

resp.json()['response']['docs'][0]['web_url']

Key: Date 	 Value: Thu, 28 Mar 2019 03:10:27 GMT
Key: Content-Type 	 Value: application/json
Key: Transfer-Encoding 	 Value: chunked
Key: Connection 	 Value: keep-alive
Key: x-amz-id-2 	 Value: M9e3iGVnPDVLTm60zfaYBI7RO6qIULs564GUMcQIporbVT7oYhIgDZ442rNKJatmHYJHlPs1GqE=
Key: x-amz-request-id 	 Value: 6F2C0AADA6654C5C
Key: Last-Modified 	 Value: Thu, 01 Jun 2017 19:32:02 GMT
Key: ETag 	 Value: "fc608e5d0d5c25a83e7de9278e6e26c7"
Key: Cache-Control 	 Value: max-age=43200
Key: Expires 	 Value: Fri, 02 Jun 2017 07:32:01 GMT
Key: Server 	 Value: AmazonS3
Key: Content-Encoding 	 Value: gzip
Key: Accept-Ranges 	 Value: bytes
Key: Via 	 Value: 1.1 varnish
Key: Age 	 Value: 1
Key: X-Served-By 	 Value: cache-bwi5043-BWI
Key: X-Cache 	 Value: MISS
Key: X-Cache-Hits 	 Value: 0
Key: X-Timer 	 Value: S1553742627.554721,VS0,VE1079
Key: Vary 	 Value: Origin, Access-Control-Request-Headers, Access-Control-Request-Method, Accept-Encoding
Key: Access-Control-Allow-Origin 	 Value: *
Key: Access-Control-All

NameError: name 'resp' is not defined

In [3]:
with open('response.json') as json_file:  
    data = json.load(json_file)


In [6]:
data.keys()

dict_keys(['meta', 'docs'])

In [8]:
data['meta']

{'hits': 6977}

In [19]:
keys = data['docs'][0].keys()

dict_keys(['web_url', 'snippet', 'lead_paragraph', 'print_page', 'blog', 'source', 'multimedia', 'headline', 'keywords', 'pub_date', 'document_type', 'news_desk', 'section_name', 'byline', 'type_of_material', '_id', 'word_count', 'score', 'uri'])

In [17]:
for key, value in data['docs'][0].items():
    print("Key = {}, Value = {}".format(key, value))

Key = web_url, Value = https://www.nytimes.com/2019/01/02/obituaries/daryl-dragon-dead.html
Key = snippet, Value = He and his wife, Toni Tennille, were one of the most successful hit-making combinations of the 1970s. Their “Love Will Keep Us Together” went to No. 1.
Key = lead_paragraph, Value = He and his wife, Toni Tennille, were one of the most successful hit-making combinations of the 1970s. Their “Love Will Keep Us Together” went to No. 1.
Key = print_page, Value = 10
Key = blog, Value = []
Key = source, Value = The New York Times
Key = multimedia, Value = [{'rank': 0, 'subtype': 'xlarge', 'caption': None, 'credit': None, 'type': 'image', 'url': 'images/2019/01/03/obituaries/03DRAGON1-print/merlin_148690920_b809ab8a-e519-4e75-8770-9d43fe082f7c-articleLarge.jpg', 'height': 446, 'width': 600, 'legacy': {'xlarge': 'images/2019/01/03/obituaries/03DRAGON1-print/merlin_148690920_b809ab8a-e519-4e75-8770-9d43fe082f7c-articleLarge.jpg', 'xlargewidth': 600, 'xlargeheight': 446}, 'subType': 

In [51]:
df = pd.DataFrame.from_dict(data['docs'])

_id blog  \
0     5c2d52db3a125f5075c029ae   []   
1     5c2d38833a125f5075c02974   []   
2     5c2cee413a125f5075c028db   []   
3     5c2d02703a125f5075c028fd   []   
4     5c2d03dd3a125f5075c02901   []   
5     5c2da4e73a125f5075c02a12   []   
6     5c2cb0933a125f5075c0286f   []   
7     5c2e2f0f3a125f5075c02b01   []   
8     5c2d3b713a125f5075c0297f   []   
9     5c2af8393a125f5075c026c9   []   
10    5c2b01e63a125f5075c026d3   []   
11    5c2ab6b83a125f5075c02693   []   
12    5c2abdb83a125f5075c0269d   []   
13    5c2ba7a53a125f5075c0275b   []   
14    5c2ac5f13a125f5075c026a3   []   
15    5c2cd8e83a125f5075c028aa   []   
16    5c2d220f3a125f5075c02940   []   
17    5c2e38bf3a125f5075c02b1e   []   
18    5c2ddd313a125f5075c02a6e   []   
19    5c2b16fe3a125f5075c026df   []   
20    5c2bcaef3a125f5075c0277f   []   
21    5c2c39dc3a125f5075c027d1   []   
22    5c2bca483a125f5075c0277e   []   
23    5c2c99b63a125f5075c02851   []   
24    5c2d35393a125f5075c0296d   []   
25    5c2bac343a125f5075c02764   []   
26    5c2ddd2f3a125f5075c02a6d   []   
27    5c2e611e3a125f5075c02b86   []   
28    5c2e62b03a125f5075c02b8a   []   
29    5c2e608a3a125f5075c02b84   []   
...                        ...  ...   
6947  5c5280d73a125f5075c073b9   []   
6948  5c5392be3a125f5075c076e9   []   
6949  5c5392c43a125f5075c076ea   []   
6950  5c5392d23a125f5075c076ef   []   
6951  5c5326f23a125f5075c07564   []   
6952  5c52fd443a125f5075c074ec   []   
6953  5c53adab3a125f5075c07735   []   
6954  5c53e9463a125f5075c077b0   []   
6955  5c52c7393a125f5075c07456   []   
6956  5c5312b13a125f5075c0752b   []   
6957  5c53044b3a125f5075c074fe   []   
6958  5c52c3a23a125f5075c07442   []   
6959  5c5274e83a125f5075c073b2   []   
6960  5c53242d3a125f5075c07560   []   
6961  5c530dfa3a125f5075c07520   []   
6962  5c53458b3a125f5075c075d7   []   
6963  5c53066e3a125f5075c07502   []   
6964  5c53451b3a125f5075c075d4   []   
6965  5c5333f03a125f5075c07588   []   
6966  5c5333f03a125f5075c07588   []   
6967  5c535cb23a125f5075c0764c   []   
6968  5c53d2713a125f5075c07778   []   
6969  5c538d533a125f5075c076db   []   
6970  5c52ca953a125f5075c07465   []   
6971  5c53890e3a125f5075c076d3   []   
6972  5c535cdf3a125f5075c0764e   []   
6973  5c536fe63a125f5075c0767c   []   
6974  5c53e0a03a125f5075c07793   []   
6975  5c53fc883a125f5075c077de   []   
6976  5c52c7233a125f5075c0744b   []   

                                                 byline document_type  \
0     {'original': 'By NEIL GENZLINGER', 'person': [...       article   
1     {'original': 'By CHRISTINA ANDERSON', 'person'...       article   
2     {'original': 'By TRIP GABRIEL', 'person': [{'f...       article   
3     {'original': None, 'person': None, 'organizati...       article   
4     {'original': None, 'person': None, 'organizati...       article   
5     {'original': 'By GABE COHN', 'person': [{'firs...       article   
6     {'original': 'By KAI SCHULTZ and AYESHA VENKAT...       article   
7     {'original': 'By PHILIP GALANES', 'person': [{...       article   
8     {'original': 'By WHITSON GORDON', 'person': [{...       article   
9     {'original': None, 'person': None, 'organizati...       article   
10    {'original': 'By LAUREN MESSMAN', 'person': [{...       article   
11    {'original': None, 'person': None, 'organizati...       article   
12    {'original': None, 'person': None, 'organizati...       article   
13    {'original': 'By PAUL KRUGMAN', 'person': [{'f...       article   
14    {'original': 'By MOTOKO RICH and DAVID E. SANG...       article   
15    {'original': 'By JULIE HIRSCHFELD DAVIS and MI...       article   
16    {'original': 'By MARTHA SCHWENDENER', 'person'...       article   
17    {'original': 'By ADAM NOSSITER', 'person': [{'...       article   
18    {'original': 'By ERNESTO LONDOÑO', 'person': [...       article   
19    {'original': 'By RACHEL NUWER', 'person': [{'f...       article   
20    {'original': 'By EMMA G. FITZSIMMONS', 'person...       article   
21